In [1]:
import os
import sys
# sys.path.insert(0, "/home/axiwa/Learn/CG/covariance/mipmap/build/python")
import mitsuba as mi
import drjit as dr
from matplotlib import pyplot as plt
import numpy as np
mi.set_variant('cuda_ad_rgb')
from mitsuba.python.util import traverse

In [2]:
def mse(image, image_ref):
    return dr.mean(dr.sqr(image - image_ref))

In [3]:
# a = mi.Float([2])
# dr.enable_grad(a)

# b = a
# c = 2 * b

# dr.set_label(a, 'a')
# dr.set_label(b, 'b')
# dr.set_label(c, 'c')

# dr.set_grad(b, 2)
# dr.backward(b, flags=dr.ADFlag.ClearNone)

# print (dr.grad(a))

# graph = dr.graphviz_ad()
# graph.render('mipmap.dot')

[1.0]


## Camera, Emitter

In [4]:
# Camera
sensor = mi.load_string('<sensor version="3.0.0" type="perspective" id="sensor">  \
        <float name="fov" value="35"/> <float name="near_clip" value="0.10000000149011612"/> \
		<float name="far_clip" value="1000.0"/> \
        <transform name="to_world"> \
            <lookat target="0, 2, 0" origin="0, 2, -50" up="0, 1, 0"/> \
            <rotate y="1" angle="22.5"/> \
        </transform> \
        <sampler type="independent"> \
            <integer name="sample_count" value="8"/> \
        </sampler> \
        <film type="hdrfilm"> \
            <integer name="width"  value="1024"/> \
            <integer name="height" value="1024"/> \
            <rfilter type="gaussian"/> \
            <string name="pixel_format" value="rgb"/> \
        </film> \
    </sensor>')

# Light
emitter = mi.load_string('\
    <emitter version = "3.0.0" type="directional"> \
        <rgb name="irradiance" value="2"/> \
        <vector name="direction" value="0, -1, -1"/> \
    </emitter> ')


## My mipmap plugin

In [21]:
# BSDF
ctx = mi.BSDFContext()

bsdf = mi.load_dict({      
    'type': 'diffuse',
    'reflectance': {
        'type': 'mipmap',
        'filename': 'figures/white200.png',
        'filter_type': 'bilinear',
        'wrap_mode': 'repeat',
#         'mipmap_filter_type': 'trilinear',
        'to_uv': mi.ScalarTransform4f.scale([4, 4, 1])
    }
})

MIPMAP BUILT SUCCESS


## Scene, Shape

In [22]:
# Obj
floor = mi.load_dict({
    'type': 'obj',
    'filename': 'figures/meshes/Plane.obj', 
    'bsdf': bsdf
})

# Scene
scene = mi.load_dict({
    "type" : "scene",
    'integrator': { 'type': 'direct' },
    "sensor": sensor,
    "emitter": emitter,
    "obj": floor,
})

## Traverse

In [32]:
params = mi.traverse(scene)
print (params)

key = 'obj.bsdf.reflectance.data'
dr.set_label(params[key], 'myTexture')
dr.enable_grad(params[key])
dr.enable_grad(params['obj.bsdf.reflectance.data2'])
dr.enable_grad(params['obj.bsdf.reflectance.data3'])
dr.enable_grad(params['obj.bsdf.reflectance.data4'])

params.update();
print (dr.grad_enabled(params[key]))
print (dr.grad_enabled(params['obj.bsdf.reflectance.data3']))

SceneParameters[
  ---------------------------------------------------------------------------------
  Name                          Flags    Type  Parent
  ---------------------------------------------------------------------------------
  emitter.irradiance.value      ∂        Color3f SRGBReflectanceSpectrum
  emitter.to_world                       Transform4f DirectionalEmitter
  obj.bsdf.reflectance.data     ∂        TensorXf MIPMapTexture
  obj.bsdf.reflectance.data2    ∂        TensorXf MIPMapTexture
  obj.bsdf.reflectance.data3    ∂        TensorXf MIPMapTexture
  obj.bsdf.reflectance.data4    ∂        TensorXf MIPMapTexture
  obj.bsdf.reflectance.to_uv             ScalarTransform3f MIPMapTexture
  obj.vertex_count                       int   OBJMesh
  obj.face_count                         int   OBJMesh
  obj.faces                              UInt  OBJMesh
  obj.vertex_positions          ∂, D     Float OBJMesh
  obj.vertex_normals            ∂, D     Float OBJMesh
  obj.vertex

In [37]:
mi.Bitmap(params[key])

Bitmap[
  pixel_format = y,
  component_format = float32,
  size = [200, 200],
  srgb_gamma = 0,
  struct = Struct<4>[
    float32 Y; // @0, premultiplied alpha
  ],
  data = [ 156 KiB of image data ]
]

In [ ]:
mi.Bitmap(params['obj.bsdf.reflectance.data4'])

In [33]:
graph = dr.graphviz_ad()
graph.render('mipmap.dot')

'mipmap.dot.pdf'

In [9]:
# Reference image and ref texture
image_ref = mi.Bitmap('figures/mi_ref.exr')
ref_tex = mi.load_dict({
        'type': 'bitmap',
        'filename': 'figures/smallcheck.png',
        'filter_type': 'bilinear',
        'wrap_mode': 'repeat',
#         'mipmap_filter_type': 'ewa',
        'to_uv': mi.ScalarTransform4f.scale([16, 16, 1])
    })
ref_param = traverse(ref_tex)
m_texture = ref_param['data']
dr.detach(m_texture)
mi.Bitmap(image_ref)

Bitmap[
  pixel_format = rgb,
  component_format = float16,
  size = [1024, 1024],
  srgb_gamma = 0,
  struct = Struct<6>[
    float16 R; // @0, premultiplied alpha
    float16 G; // @2, premultiplied alpha
    float16 B; // @4, premultiplied alpha
  ],
  data = [ 6 MiB of image data ]
]

In [24]:
iteration_count = 1
errors = []

image = mi.render(scene, params, spp=4)

# Evaluate the objective function from the current rendered image
loss = mse(image, image_ref)

# Backpropagate through the rendering process
print (loss)
dr.backward(loss)

grad = dr.grad(params[key])
grad *= 1e5

# Track the difference between the current color and the true value
err_ref = dr.mean(dr.sqr(m_texture- params[key]))
# print(f"Iteration {it:02d}: parameter error = {err_ref[0]:6f}", end='\r')
errors.append(err_ref)

print('\nOptimization complete.')
print (grad.array)
mi.util.convert_to_bitmap(grad)

[0.04556407034397125]

Optimization complete.
[0.0, 0.0, 0.0, 0.0, 0.0, .. 39990 skipped .., 0.0, 0.0, 0.0, 0.0, 0.0]


Bitmap[
  pixel_format = rgb,
  component_format = uint8,
  size = [200, 200],
  srgb_gamma = 1,
  struct = Struct<3>[
    uint8 R; // @0, normalized, gamma, premultiplied alpha
    uint8 G; // @1, normalized, gamma, premultiplied alpha
    uint8 B; // @2, normalized, gamma, premultiplied alpha
  ],
  data = [ 117 KiB of image data ]
]

In [25]:
graph = dr.graphviz_ad()
graph.render('mipmap2')

'mipmap2.pdf'

In [11]:
## Show loss-iteration
# plt.plot(errors)
# plt.xlabel('Iteration'); plt.ylabel('MSE(param)'); plt.title('Parameter error plot');
# plt.show()

In [34]:
dr.set_grad(params[key], 1)
grad = dr.grad(params[key])
print (grad.array)

dr.forward(params[key], flags=dr.ADFlag.ClearNone)
grad = dr.grad(params['obj.bsdf.reflectance.data4'])
print (dr.grad_enabled(params['obj.bsdf.reflectance.data4']))
print (grad.array)

[1.0, 1.0, 1.0, 1.0, 1.0, .. 39990 skipped .., 1.0, 1.0, 1.0, 1.0, 1.0]
True
[0.0, 0.0, 0.0, 0.0, 0.0, .. 39990 skipped .., 0.0, 0.0, 0.0, 0.0, 0.0]


In [36]:
print (params['obj.bsdf.reflectance.data4'].array)

[1.0, 1.0, 1.0, 1.0, 1.0, .. 39990 skipped .., 1.0, 1.0, 1.0, 1.0, 1.0]


## Tensor test

In [17]:
import os
import sys
# sys.path.insert(0, "/home/axiwa/Learn/CG/covariance/mipmap/build/python")
import mitsuba as mi
import drjit as dr
from matplotlib import pyplot as plt
mi.set_variant('cuda_ad_rgb')
from mitsuba.python.util import traverse

In [17]:
# Tensor
b = mi.load_dict({
        'type': 'bitmap',
        'filename': 'figures/color.png',
        'filter_type': 'bilinear',
        'wrap_mode': 'repeat',
#         'mipmap_filter_type': 'ewa',
        'to_uv': mi.ScalarTransform4f.scale([1, 1, 1])
})
src = mi.traverse(b)['data']
pi = mi.Float(src.array[0])
dr.set_label(pi, 'pi')
dr.enable_grad(pi)
dr.scatter(src.array, pi, 0)
print (src)
mi.Bitmap(src)

2023-03-16 00:57:36 WARN main [bitmap.cpp:1630] libpng warning: Interlace handling should be turned on when using png_read_image

TensorXf(shape=(1059, 1044, 3))


Bitmap[
  pixel_format = rgb,
  component_format = float32,
  size = [1044, 1059],
  srgb_gamma = 0,
  struct = Struct<12>[
    float32 R; // @0, premultiplied alpha
    float32 G; // @4, premultiplied alpha
    float32 B; // @8, premultiplied alpha
  ],
  data = [ 12.7 MiB of image data ]
]

In [18]:
print (dr.width(src.array))

3316788


In [19]:
def index(i, j, res):
    channel = res[2]
    i = dr.clamp(i, 0, res[0]-1)
    j = dr.clamp(j, 0, res[1]-1)
    return channel * (i * res[1] + j)

def downsample_trivial(src):
    assert len(src.shape) == 3

    target_res = (src.shape[0]//2, src.shape[1]//2, src.shape[2])
    print (target_res)
    dst_array = dr.zeros(mi.Float, target_res[0] * target_res[1] * target_res[2])
    dst = dr.zeros(type(src), target_res)

    y, x = dr.meshgrid(
            dr.arange(mi.UInt, target_res[1]), # 0,1,2,3
            dr.arange(mi.UInt, target_res[0])  # 0,0,0,0...1,1,1...2,2,2...
    )
    
    dx = [0, 0, 1, 1]
    dy = [0, 1, 0, 1]
    for i in range(4):
        x_ = dr.clamp(2*x+dx[i], 0, src.shape[0]-1)
        y_ = dr.clamp(2*y+dy[i], 0, src.shape[1]-1)
        index = (x_ * src.shape[1] + y_) * target_res[2]
        a, b = dr.meshgrid(
            dr.arange(mi.UInt, target_res[2]),
            index
        )
        dst_array += dr.gather(mi.Float, src.array, a+b)

    dst_array /= 4
    dst = type(src)(dst_array, target_res)

## WRONG. Avoid using Python iteration...
#     for i in range(target_res[0]):
#         for j in range(target_res[1]):
#             for c in range(target_res[2]):
#                 dst[i, j, c] = \
#                     (dr.gather(mi.Float, src.array, index(2*i, 2*j, src.shape) + c) + \
#                     dr.gather(mi.Float, src.array, index(2*i+1, 2*j, src.shape) + c) + \
#                     dr.gather(mi.Float, src.array, index(2*i, 2*j+1, src.shape) + c) + \
#                     dr.gather(mi.Float, src.array, index(2*i+1, 2*j+1, src.shape) + c)) * 0.25

    return dst

In [20]:
dst = downsample_trivial(src)
mi.Bitmap(dst)

(529, 522, 3)


Bitmap[
  pixel_format = rgb,
  component_format = float32,
  size = [522, 529],
  srgb_gamma = 0,
  struct = Struct<12>[
    float32 R; // @0, premultiplied alpha
    float32 G; // @4, premultiplied alpha
    float32 B; // @8, premultiplied alpha
  ],
  data = [ 3.16 MiB of image data ]
]

In [21]:
dst2 = downsample_trivial(dst)
print (dr.grad_enabled(dst2))
mi.Bitmap(dst2)

(264, 261, 3)
True


Bitmap[
  pixel_format = rgb,
  component_format = float32,
  size = [261, 264],
  srgb_gamma = 0,
  struct = Struct<12>[
    float32 R; // @0, premultiplied alpha
    float32 G; // @4, premultiplied alpha
    float32 B; // @8, premultiplied alpha
  ],
  data = [ 807 KiB of image data ]
]

In [22]:
dst3 = downsample_trivial(dst2)
print (dr.grad_enabled(dst3))
mi.Bitmap(dst3)

(132, 130, 3)
True


Bitmap[
  pixel_format = rgb,
  component_format = float32,
  size = [130, 132],
  srgb_gamma = 0,
  struct = Struct<12>[
    float32 R; // @0, premultiplied alpha
    float32 G; // @4, premultiplied alpha
    float32 B; // @8, premultiplied alpha
  ],
  data = [ 201 KiB of image data ]
]

In [23]:
dr.set_grad(pi, 1)
dr.forward_from(pi, flags=dr.ADFlag.ClearNone)
# graph = dr.graphviz_ad()
# graph.render('mipmap.dot')
print (dr.grad(dst).numpy()[0, 0])

[0.25 0.   0.  ]


In [24]:
ref = dr.zeros(type(src), dst3.shape)

In [25]:
def mse(image, image_ref):
    return dr.mean(dr.sqr(image - image_ref))

In [26]:
loss = mse(ref, dst3)

In [27]:
dr.backward(loss, flags=dr.ADFlag.ClearNone)

In [28]:
grad3 = dr.grad(dst3)
grad3 *= 1e4
mi.Bitmap(grad3)

Bitmap[
  pixel_format = rgb,
  component_format = float32,
  size = [130, 132],
  srgb_gamma = 0,
  struct = Struct<12>[
    float32 R; // @0, premultiplied alpha
    float32 G; // @4, premultiplied alpha
    float32 B; // @8, premultiplied alpha
  ],
  data = [ 201 KiB of image data ]
]

In [29]:
grad2 = dr.grad(dst2)
grad2 *= 1e4
mi.Bitmap(grad2)

Bitmap[
  pixel_format = rgb,
  component_format = float32,
  size = [261, 264],
  srgb_gamma = 0,
  struct = Struct<12>[
    float32 R; // @0, premultiplied alpha
    float32 G; // @4, premultiplied alpha
    float32 B; // @8, premultiplied alpha
  ],
  data = [ 807 KiB of image data ]
]